<a href="https://colab.research.google.com/github/benny-png/Swahili-model-for-Audio-Text-to-Speech/blob/main/ASR_swahili_mozilla_Voice.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.3/474.3 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 16.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 13.2 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.


In [5]:
!git config --global credential.helper store
!huggingface-cli login



    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|
    
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) y
Token is valid (permission: fineGrained).
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [4]:
import os
from typing import List, Dict
from datasets import load_dataset, Dataset, Audio
from huggingface_hub import HfApi, create_repo

In [14]:
def create_dataset_entries(filtered_dataset) -> List[Dict]:
    """Create dataset entries based on the filtered dataset."""
    data = []
    for i, item in enumerate(filtered_dataset):
        entry = {
            'line_id': f"SW{i:04d}",
            'audio': item['path'],
            'text': item['sentence'],
            'speaker_id': item['client_id'],

        }
        data.append(entry)
    return data

def upload_to_huggingface(dataset: Dataset, repo_id: str) -> None:
    """Upload the dataset to Hugging Face."""
    api = HfApi()

    try:
        create_repo(repo_id=repo_id, repo_type="dataset")
        print("Repository created successfully.")
    except Exception as e:
        print(f"Repository creation failed or already exists: {e}")

    dataset.push_to_hub(repo_id)
    print("Dataset uploaded successfully!")

In [15]:
def create_and_upload_swahili_dataset(repo_id: str, client_id: str) -> None:
    """
    Create a dataset from the Mozilla Common Voice Swahili dataset for a specific client_id and upload it to Hugging Face.
    """
    # Load the Swahili dataset
    original_dataset = load_dataset("mozilla-foundation/common_voice_17_0", "sw")

    # Filter the dataset for the specific client_id
    filtered_dataset = original_dataset.filter(lambda example: example['client_id'] == client_id)

    # Print the number of rows after filtering
    print(f"Number of rows for client ID {client_id}: {len(filtered_dataset['train'])}")

    # Create dataset entries
    data = create_dataset_entries(filtered_dataset["train"])

    # Create Dataset
    dataset = Dataset.from_dict({
        'line_id': [item['line_id'] for item in data],
        'audio': [item['audio'] for item in data],
        'text': [item['text'] for item in data],
        'speaker_id': [item['speaker_id'] for item in data],

    })

    # Cast the audio column to Audio type
    dataset = dataset.cast_column("audio", Audio(sampling_rate=48000))  # Adjust sampling rate if needed

    # Upload to Hugging Face
    upload_to_huggingface(dataset, repo_id)

In [16]:
# Example usage
specific_client_id = "052c5091df7681302a2117b2d21db1540c2156f5254ebe9876a7d0146588eab582e11cb47761a18f84200a510a5386bdf024374f76113cd15fe1cc8d7b9fcf0b"
create_and_upload_swahili_dataset("swahili-common-voice-woman_sound", specific_client_id)

Number of rows for client ID 052c5091df7681302a2117b2d21db1540c2156f5254ebe9876a7d0146588eab582e11cb47761a18f84200a510a5386bdf024374f76113cd15fe1cc8d7b9fcf0b: 151
Repository created successfully.


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Map:   0%|          | 0/151 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Dataset uploaded successfully!


### FINE TUNING TTS using "Benjamin-png/swahili-common-voice-woman_sound"



In [1]:
!pip uninstall transformers datasets accelerate # remove the ones installed when you run pip install -r requirements.txt

!pip install transformers==4.35.1 datasets[audio]==2.14.7 accelerate==0.24.1

# https://github.com/ylacombe/finetune-hf-vits/issues/40

Found existing installation: transformers 4.44.2
Uninstalling transformers-4.44.2:
  Would remove:
    /usr/local/bin/transformers-cli
    /usr/local/lib/python3.10/dist-packages/transformers-4.44.2.dist-info/*
    /usr/local/lib/python3.10/dist-packages/transformers/*
Proceed (Y/n)? y
  Successfully uninstalled transformers-4.44.2
Found existing installation: accelerate 0.34.2
Uninstalling accelerate-0.34.2:
  Would remove:
    /usr/local/bin/accelerate
    /usr/local/bin/accelerate-config
    /usr/local/bin/accelerate-estimate-memory
    /usr/local/bin/accelerate-launch
    /usr/local/bin/accelerate-merge-weights
    /usr/local/lib/python3.10/dist-packages/accelerate-0.34.2.dist-info/*
    /usr/local/lib/python3.10/dist-packages/accelerate/*
Proceed (Y/n)? y
  Successfully uninstalled accelerate-0.34.2
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.1/123.1 kB 11.3 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible wi

In [2]:
!git clone https://github.com/ylacombe/finetune-hf-vits.git
%cd finetune-hf-vits
!pip install -r requirements.txt


Cloning into 'finetune-hf-vits'...
remote: Enumerating objects: 173, done.
remote: Counting objects: 100% (41/41), done.
remote: Compressing objects: 100% (15/15), done.
remote: Total 173 (delta 30), reused 30 (delta 26), pack-reused 132 (from 1)
Receiving objects: 100% (173/173), 1.27 MiB | 18.86 MiB/s, done.
Resolving deltas: 100% (92/92), done.
/content/finetune-hf-vits
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 65.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 19.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 311.4/311.4 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 6.6 MB/s eta 0:00:00


In [3]:
%cd /content/finetune-hf-vits/monotonic_align
!mkdir monotonic_align
!python setup.py build_ext --inplace
%cd ..



/content/finetune-hf-vits/monotonic_align
Compiling core.pyx because it changed.
[1/1] Cythonizing core.pyx
/usr/local/lib/python3.10/dist-packages/Cython/Compiler/Main.py:381: FutureWarning: Cython directive 'language_level' not set, using '3str' for now (Py3). This has changed from earlier releases! File: /content/finetune-hf-vits/monotonic_align/core.pyx
  tree = Parsing.p_module(s, pxd, full_module_name)
performance hint: core.pyx:7:5: Exception check on 'maximum_path_each' will always require the GIL to be acquired.
Possible solutions:
	1. Declare 'maximum_path_each' as 'noexcept' if you control the definition and you're sure you don't want the function to raise exceptions.
	2. Use an 'int' return type on 'maximum_path_each' to allow an error code to be returned.
performance hint: core.pyx:38:6: Exception check on 'maximum_path_c' will always require the GIL to be acquired.
Possible solutions:
	1. Declare 'maximum_path_c' as 'noexcept' if you control the definition and you're sure

In [4]:
# Clone the repository and navigate to the directory
!git clone https://github.com/isi-nlp/uroman.git
%cd uroman

# Set the UROMAN environment variable
%env UROMAN=$(pwd)

# Install dependencies
!apt-get install -y festival espeak-ng mbrola

# Install phonemizer
!pip install phonemizer


Cloning into 'uroman'...
remote: Enumerating objects: 579, done.
remote: Counting objects: 100% (295/295), done.
remote: Compressing objects: 100% (125/125), done.
remote: Total 579 (delta 189), reused 262 (delta 164), pack-reused 284 (from 1)
Receiving objects: 100% (579/579), 5.07 MiB | 18.80 MiB/s, done.
Resolving deltas: 100% (321/321), done.
/content/finetune-hf-vits/uroman
env: UROMAN=$(pwd)
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  alsa-utils espeak-ng-data festlex-cmu festlex-poslex festvox-kallpc16k libatopology2
  libespeak-ng1 libestools2.5 libfftw3-single3 libpcaudio0 libsonic0 sgml-base
Suggested packages:
  dialog pidgin-festival festival-freebsoft-utils libfftw3-bin libfftw3-dev mbrola-voice cicero
  sgml-base-doc
The following NEW packages will be installed:
  alsa-utils espeak-ng espeak-ng-data festival festlex-cmu festlex-poslex festvox-kallpc16k
  libatopolog

In [7]:
import os
import json

# Configuration details
config = {
    "project_name": "mozilla_lady_swahili_vocals",
    "push_to_hub": True,
    "hub_model_id": "Benjamin-png/swahili-mms-tts-mozilla-lady-voice-finetuned",
    "overwrite_output_dir": True,
    "output_dir": "/content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/mms-tts-finetuned",

    "dataset_name": "Benjamin-png/swahili-common-voice-woman_sound", # Updated path
    "audio_column_name": "audio",
    "text_column_name": "text",
    "train_split_name": "train",
    "eval_split_name": "train",
    "speaker_id_column_name": "speaker_id",
    "override_speaker_embeddings": True,
    "filter_on_speaker_id": "052c5091df7681302a2117b2d21db1540c2156f5254ebe9876a7d0146588eab582e11cb47761a18f84200a510a5386bdf024374f76113cd15fe1cc8d7b9fcf0b",

    "max_duration_in_seconds": 20,
    "min_duration_in_seconds": 1.0,
    "max_tokens_length": 500,

    "model_name_or_path": "Benjamin-png/swa-checkpoint",

    "preprocessing_num_workers": 4,

    "do_train": True,
    "num_train_epochs": 200,
    "gradient_accumulation_steps": 1,
    "gradient_checkpointing": False,
    "per_device_train_batch_size": 16,
    "learning_rate": 2e-5,
    "adam_beta1": 0.8,
    "adam_beta2": 0.99,
    "warmup_ratio": 0.01,
    "group_by_length": False,

    "do_eval": True,
    "eval_steps": 50,
    "per_device_eval_batch_size": 16,
    "max_eval_samples": 25,
    "do_step_schedule_per_epoch": True,

    "weight_disc": 3,
    "weight_fmaps": 1,
    "weight_gen": 1,
    "weight_kl": 1.5,
    "weight_duration": 1,
    "weight_mel": 35,

    "fp16": True,
    "seed": 456
}

# Save configuration to JSON file
config_dir = "/content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE"
config_filename = os.path.join(config_dir, "Mozilla_lady_swahili_vocals_config.json")

with open(config_filename, 'w') as config_file:
    json.dump(config, config_file, indent=4)

print(f"Configuration file saved at: {config_filename}")

# !accelerate launch /content/finetune-hf-vits/run_vits_finetuning.py /content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/Mozilla_lady_swahili_vocals_config.json


Configuration file saved at: /content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/Mozilla_lady_swahili_vocals_config.json


# FINETUNING

In [8]:
!accelerate launch /content/finetune-hf-vits/run_vits_finetuning.py /content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/Mozilla_lady_swahili_vocals_config.json


/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:441: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
The following values were not passed to `accelerate launch` and had defaults used instead:
	`--num_processes` was set to a value of `1`
	`--num_machines` was set to a value of `1`
	`--mixed_precision` was set to a value of `'no'`
	`--dynamo_backend` was set to a value of `'no'`
To avoid this warning pass in values for each of the problematic parameters or run `accelerate config`.
/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:441: FutureWarning: `torch.utils._pytree._reg

### TESTING THE MODEL

In [9]:
from transformers import VitsModel, AutoTokenizer
import torch
import numpy as np
import scipy.io.wavfile

/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:441: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
/usr/local/lib/python3.10/dist-packages/transformers/utils/generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(


In [10]:

# Load model and tokenizer
model = VitsModel.from_pretrained("Benjamin-png/swahili-mms-tts-mozilla-lady-voice-finetuned")
tokenizer = AutoTokenizer.from_pretrained("Benjamin-png/swahili-mms-tts-mozilla-lady-voice-finetuned")

In [11]:


# Running the TTS
text = """Neurotech Africa ni kampuni kutoka Tanzania inaongoza mapinduzi ya kidigitali nchini na barani Afrika kwa suluhisho za Akili bandia (AI).
Tunajenga AI ambayo inasaidia biashara kuboresha uzoefu wa wateja kupitia teknolojia za kisasa za mazungumzo.
Tuna timu ya wataalamu wanaojitahidi kuboresha huduma za afya, kuchambua data, na kuleta uvumbuzi barani Afrika.
Lengo letu ni kuboresha mawasiliano ya wateja kwa kutumia AI na kusaidia biashara kufanikisha malengo yao.
Kupitia Sarufi, tunawezesha biashara na watengenezaji kujenga chatbots za AI bila ujuzi wa programu.
Sarufi inaruhusu uundaji wa chatbots kwa mitandao mbalimbali ya kijamii kama WhatsApp, Facebook, na Instagram.
Pia tunaendesha mikutano na hackathons za AI ili kuwajengea uwezo wanajamii na kuongeza ushirikiano."""
inputs = tokenizer(text, return_tensors="pt")

# Generate waveform
with torch.no_grad():
    output = model(**inputs).waveform

# Convert PyTorch tensor to NumPy array
output_np = output.squeeze().cpu().numpy()

# Write to WAV file
scipy.io.wavfile.write("/content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/Custom_lady_tts_neurotech.wav", rate=model.config.sampling_rate, data=output_np)






In [12]:
# To play the audio in Colab
from IPython.display import Audio
Audio('/content/drive/MyDrive/AUDIO-API_MOZILLA__LADY_VOICE/Custom_lady_tts_neurotech.wav', rate=16000)